In [1]:
#Variabilil globali
width = 256
height = 256
mean_pre_trained =[0.485, 0.456, 0.406]
std_pre_trained =[0.229, 0.224, 0.225]
num_classes = 153
training = True

# TODO:
- Far partire Visdom
- Data agumentation
- Aumentare il knn con data agumentation.
- Allenare con nostre foto.



# Domande al prof:
- Perchè cambiando le dimensioni, aumentandole e diminuendole, l'accuracy cambia anche di molto?

# Import necessari

In [2]:
import torchvision.models as models
from torch.utils.data.dataset import Dataset
from PIL import Image
from os import path as pathFunction
from torchvision import transforms
import numpy as np
import torch
from torch.utils.data import DataLoader
import torch.nn as nn
import pandas as pd
from sklearn.neighbors import KNeighborsClassifier as KNN
from torch.autograd import Variable
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import confusion_matrix
from sklearn.metrics import recall_score
from sklearn.metrics import f1_score
from torch.optim import SGD
from torch.autograd import Variable
from torchnet.logger import VisdomPlotLogger, VisdomSaver
from torchnet.meter import AverageValueMeter
from pathlib import Path


# Classe per la gestione del dataset

In [3]:
np.random.seed(1234)
torch.random.manual_seed(1234);

class ScenesDataset(Dataset):
    def __init__(self,base_path,txt_list,transform=None):
        #conserviamo il path alla cartella contenente le immagini
        self.base_path=base_path
        #carichiamo la lista dei file
        #sarà una matrice con n righe (numero di immagini) e 2 colonne (path, etichetta)
        self.images = np.loadtxt(txt_list,dtype=str,delimiter=',')
        #print("self.images ha i seguenti elementi:", len(self.images))
        #conserviamo il riferimento alla trasformazione da applicare
        self.transform = transform
    def __getitem__(self, index):
        #print("Get item numero -->", index)
        #recuperiamo il path dell'immagine di indice index e la relativa etichetta
        f,c = self.images[index]
        #carichiamo l'immagine utilizzando PIL e facciamo il resize a 3 canali.
        im = Image.open(pathFunction.join(self.base_path, f)).convert("RGB")
        
        #Resize:
        im = im.resize((width,height))
        #se la trasfromazione è definita, applichiamola all'immagine
        if self.transform is not None:
            im = self.transform(im)       
        
        #convertiamo l'etichetta in un intero
        label = int(c)
        #restituiamo un dizionario contenente immagine etichetta
        #print("Mentre creo il tutto, label vale-->", label, ", name vale -->", f)
        return {'image' : im, 'label':label, 'name': f}
    #restituisce il numero di campioni: la lunghezza della lista "images"
    def __len__(self):
        #print("Ho invocato len, vale-->", len(self.images))
        return len(self.images)

# Funzione che ci restituisce media e varianza di un dataset.
- Prende in input il dataset.

In [4]:
def get_mean_devst(dataset):
    m = np.zeros(3)
    for sample in dataset:
        m+= np.array(sample['image'].sum(1).sum(1)) #accumuliamo la somma dei pixel canale per canale
    #dividiamo per il numero di immagini moltiplicato per il numero di pixel
    m=m/(len(dataset)*width*height)
    #procedura simile per calcolare la deviazione standard
    s = np.zeros(3)
    for sample in dataset:
        s+= np.array(((sample['image']-torch.Tensor(m).view(3,1,1))**2).sum(1).sum(1))
    s=np.sqrt(s/(len(dataset)*width*height))
    print("Medie",m)
    print("Dev.Std.",s)
    return m, s

# Prendiamo media e varianza per normalizzare successivamente i dati

In [5]:
#dataset = ScenesDataset('Dataset_base','train.txt',transform=transforms.ToTensor())
#m, s = get_mean_devst(dataset)

# Funzione per calcolare l'accuracy.

In [6]:
# Prende in input l'array di feature e il classificatore(knn.) 
def accuracy(classifier, samples):
    TP = 0
    TN = 0
    FP = 0
    FN = 0
    TOT = len(samples)
    for i in range(len(samples)):
        pred_label = classifier.predict(samples[i]["feature"].cpu().numpy().reshape(1, -1))
        if pred_label[0] == samples[i]["label"]:
            TP += 1
        else:
            TN += 1
        
    return float(TP)/len(samples)

In [7]:
def get_pred_label_and_target_label(classifier, samples):
    pred_label = []
    target_label = []
    for i in range(len(samples)):
        pred_label.append(classifier.predict(samples[i]["feature"].cpu().numpy().reshape(1, -1))[0])
        target_label.append(samples[i]["label"])
    return pred_label, target_label

# Funzione per estrazione feature:
- In input dataset (dataloader) e rete.

In [8]:
def extract_features(dataset, net):
    #Presa ogni riga del dataloader li passa alla net senza attivare il layer di classificazione
    feature_dataset = []
    print("Avviato extract_feature.")
    for i, dataset_train in enumerate(dataset):
        print(i, end= " ")
        x=Variable(dataset_train['image'], requires_grad=False)
        y=Variable(dataset_train['label'])
        x, y = x.cpu(), y.cpu()
        if torch.cuda.is_available():
            x, y = x.cuda(), y.cuda()
            #print("Con cuda")
        output = net(x)
        #print(output.grad, type(output.grad))

        #print("output len-->", len(output[0]), type(output), output[0], " - ", output[0].detach())
        feature_dataset.append({"label": dataset_train['label'], "feature":output[0].detach(), "name": dataset_train['name']})

    return feature_dataset

# Funzione per creare l'input per l'oggetto dataframe:
- In input dataset (dataloader) e rete.

In [9]:
def get_dataframe(dataset, net, feature_dataset = None):
    print("Avviato get_dataframe.")
    if feature_dataset == None:
        feature_dataset = extract_features(dataset, net) 
    print("\nHo concluso extract_features, sto creare feature_dataset_matrix")
    feature_dataset_matrix = np.zeros((len(feature_dataset), len(feature_dataset[0]["feature"])))    
    #Qui abbiamo nelle righe tutte le immagini, nella lable feature tutte le 9000 colonne, ossia le feature.
    label_array = np.zeros(len(feature_dataset))
    for i in range(0, len(feature_dataset)):#302
        print(i, end= " ")
        for j in range(0, len(feature_dataset[0]["feature"])):#153
            if j == 0:#salviamo la y finale nell'array label_array
                label_array[i] = feature_dataset[i]['label']
                #print(i, end= " ")
            feature_dataset_matrix[i][j] =feature_dataset[i]["feature"][j] 
        #Elimino l'elemento per cercare di risparmiare un pò di memoria.
        #feature_dataset.pop(i)
    return feature_dataset_matrix, label_array

In [10]:

def train_classification(model, train_loader, test_loader, lr=0.001, epochs=20, momentum=0.8, exp_name = 'experiment' ):
    criterion = nn.CrossEntropyLoss()
    optimizer = SGD(model.parameters(),lr, momentum=momentum)
    loaders = {'train':train_loader, 'test':test_loader}
    losses = {'train':[], 'test':[]}
    accuracies = {'train':[], 'test':[]}
    
    
    loss_meter = AverageValueMeter()
    acc_meter = AverageValueMeter()
    loss_logger = VisdomPlotLogger('line', env=exp_name, opts={'title': 'Loss', 'legend':['train','test']})
    acc_logger = VisdomPlotLogger('line', env=exp_name, opts={'title': 'Accuracy','legend':['train','test']})
    visdom_saver = VisdomSaver(envs=[exp_name])

    if torch.cuda.is_available():
        model=model.cuda()
    for e in range(epochs):
        #print("Primo ciclo for.")
        for mode in ['train', 'test']:
            #print("Secondo ciclo for.")
            
            loss_meter.reset()
            acc_meter.reset()
            
            if mode=='train':
                model.train()
            else:
                model.eval()
            epoch_loss = 0
            epoch_acc = 0
            samples = 0
            #print("Mode-->",mode)
            #print("Enumerate-->", loaders[mode])
            for i, batch in enumerate(loaders[mode]):
                #trasformiamo i tensori in variabili
                x=Variable(batch['image'], requires_grad=(mode=='train'))
                y=Variable(batch['label'])
                if torch.cuda.is_available():
                    x, y = x.cuda(), y.cuda()
                    print("Con cuda")
                #else:
                    #print("Senza cuda")
                output = model(x)
                #print(type(output))
                #print(output)
                l = criterion(output,y)
                if mode=='train':
                    l.backward()
                    optimizer.step()
                    optimizer.zero_grad()
                #print("L-->",l.item())
                acc = accuracy_score(y.cpu().data,output.cpu().max(1)[1].data)
                epoch_loss+=l.data.item()*x.shape[0]
                epoch_acc+=acc*x.shape[0]
                samples+=x.shape[0]
                print ("\r[%s] Epoch %d/%d. Iteration %d/%d. Loss: %0.2f. Accuracy: %0.2f\t\t\t\t\t" % \
                (mode, e+1, epochs, i, len(loaders[mode]), epoch_loss/samples, epoch_acc/samples),
                epoch_loss/samples,
                epoch_acc/samples,
                losses[mode].append(epoch_loss))
                accuracies[mode].append(epoch_acc)
                n = batch['image'].shape[0]
                loss_meter.add(l.item()*n,n)
                acc_meter.add(acc*n,n)
                #loss_logger.log(e+(i+1)/len(loaders[mode]), loss_meter.value()[0], name=mode)
                #acc_logger.log(e+(i+1)/len(loaders[mode]), acc_meter.value()[0], name=mode)


            loss_logger.log(e+1, loss_meter.value()[0], name=mode)
            acc_logger.log(e+1, acc_meter.value()[0], name=mode)
            
            #print("Fine secondo ciclo for")
        print("\r[%s] Epoch %d/%d. Iteration %d/%d. Loss: %0.2f. Accuracy: %0.2f\t\t\t\t\t" % \
        (mode, e+1, epochs, i, len(loaders[mode]), epoch_loss, epoch_acc))
        torch.save(model.state_dict(), "./" + exp_name + ".pth")
        print("Pesi aggiornati.")
    print("Ho finito.")
    #restituiamo il modello e i vari log
    return model, (losses, accuracies)

In [11]:
def test_model_classification(model, test_loader):
    softmax = nn.Softmax(dim=1)
    model.eval()
    model.cpu()
    preds = []
    gts = []
    for batch in test_loader:
        x=Variable(batch["image"])
        x = x.cpu()
        #applichiamo la funzione softmax per avere delle probabilità
        if torch.cuda.is_available():
            x = x.cuda()
            model.cuda()
        pred = softmax(model(x)).data.cpu().numpy().copy()
        gt = batch["label"].cpu().numpy().copy()
        #print("Pred-->", pred, ", gt-->", gt)
        preds.append(pred)
        gts.append(gt)
        #print(len(preds), len(gts))
    return np.concatenate(preds),np.concatenate(gts)

In [12]:
def test_model_classification_our_network(model, our_model, test_loader):
    softmax = nn.Softmax(dim=1)
    model.eval()
    model.cpu()
    our_model.eval()
    our_model.cpu()
    preds = []
    gts = []
    for batch in test_loader:
        x=Variable(batch["image"])
        x = x.cpu()
        #applichiamo la funzione softmax per avere delle probabilità
        if torch.cuda.is_available():
            x = x.cuda()
            model.cuda()
            our_model.cuda()
            
        pred = softmax(our_model(model(x))).data.cpu().numpy().copy()
        gt = batch["label"].cpu().numpy().copy()
        #print("Pred-->", pred, ", gt-->", gt)
        preds.append(pred)
        gts.append(gt)
        #print(len(preds), len(gts))
    return np.concatenate(preds),np.concatenate(gts)

In [13]:
def extract_features_our_network(dataset, net):
    #Presa ogni riga del dataloader li passa alla net senza attivare il layer di classificazione
    feature_dataset = []
    print("Avviato extract_feature.")
    for i, dataset_train in enumerate(dataset):
        print(i, end= " ")
        x=Variable(dataset_train["feature"], requires_grad=False)
        x = x.cpu()
        if torch.cuda.is_available():
            x = x.cuda()
        output = net(x)
        feature_dataset.append({"feature": output[0].detach(), "label":dataset_train["label"]})
    return feature_dataset

In [14]:

def train_classification_our_network(model, train_loader, test_loader, lr=0.001, epochs=20, momentum=0.8, exp_name = 'experiment' ):
    criterion = nn.CrossEntropyLoss()
    optimizer = SGD(model.parameters(),lr, momentum=momentum)
    loaders = {'train':train_loader, 'test':test_loader}
    losses = {'train':[], 'test':[]}
    accuracies = {'train':[], 'test':[]}
    
    
    loss_meter = AverageValueMeter()
    acc_meter = AverageValueMeter()
    loss_logger = VisdomPlotLogger('line', env=exp_name, opts={'title': 'Loss', 'legend':['train','test']})
    acc_logger = VisdomPlotLogger('line', env=exp_name, opts={'title': 'Accuracy','legend':['train','test']})
    visdom_saver = VisdomSaver(envs=[exp_name])

    if torch.cuda.is_available():
        model=model.cuda()
    for e in range(epochs):
        #print("Primo ciclo for.")
        for mode in ['train', 'test']:
            #print("Secondo ciclo for.")
            
            loss_meter.reset()
            acc_meter.reset()
            
            if mode=='train':
                model.train()
            else:
                model.eval()
            epoch_loss = 0
            epoch_acc = 0
            samples = 0
            #print("Mode-->",mode)
            #print("Enumerate-->", loaders[mode])
            for i, batch in enumerate(loaders[mode]):
                #trasformiamo i tensori in variabili
                x=Variable(batch['feature'], requires_grad=(mode=='train'))
                y=Variable(batch['label'])
                if torch.cuda.is_available():
                    x, y = x.cuda(), y.cuda()
                    print("Con cuda")
                #else:
                    #print("Senza cuda")
                output = model(x)
                #print(type(output))
                #print(output)
                l = criterion(output,y)
                if mode=='train':
                    l.backward()
                    optimizer.step()
                    optimizer.zero_grad()
                #print("L-->",l.item())
                acc = accuracy_score(y.cpu().data,output.cpu().max(1)[1].data)
                epoch_loss+=l.data.item()*x.shape[0]
                epoch_acc+=acc*x.shape[0]
                samples+=x.shape[0]
                print ("\r[%s] Epoch %d/%d. Iteration %d/%d. Loss: %0.2f. Accuracy: %0.2f\t\t\t\t\t" % \
                (mode, e+1, epochs, i, len(loaders[mode]), epoch_loss/samples, epoch_acc/samples),
                epoch_loss/samples,
                epoch_acc/samples,
                losses[mode].append(epoch_loss))
                accuracies[mode].append(epoch_acc)
                n = batch['feature'].shape[0]
                loss_meter.add(l.item()*n,n)
                acc_meter.add(acc*n,n)
                #loss_logger.log(e+(i+1)/len(loaders[mode]), loss_meter.value()[0], name=mode)
                #acc_logger.log(e+(i+1)/len(loaders[mode]), acc_meter.value()[0], name=mode)


            loss_logger.log(e+1, loss_meter.value()[0], name=mode)
            acc_logger.log(e+1, acc_meter.value()[0], name=mode)
            
            #print("Fine secondo ciclo for")
        print("\r[%s] Epoch %d/%d. Iteration %d/%d. Loss: %0.2f. Accuracy: %0.2f\t\t\t\t\t" % \
        (mode, e+1, epochs, i, len(loaders[mode]), epoch_loss, epoch_acc))
        torch.save(model.state_dict(), "./" + exp_name + ".pth")
        print("Pesi aggiornati.")
    print("Ho finito.")
    #restituiamo il modello e i vari log
    return model, (losses, accuracies)

# Creiamo Oggetto Dataset e dataloader, sia base che data augmentation.

In [15]:
transformss = transforms.Compose([transforms.ToTensor(), transforms.Normalize(mean_pre_trained,std_pre_trained)])
barilla_train = ScenesDataset('Dataset_base','train.txt',transform=transformss)
barilla_test = ScenesDataset('Dataset_base','test.txt',transform=transformss)
barilla_train_loader = torch.utils.data.DataLoader(barilla_train, batch_size=10, num_workers=0, shuffle=True)
barilla_test_loader = torch.utils.data.DataLoader(barilla_test, batch_size=10, num_workers=0)

In [16]:
transformss = transforms.Compose([transforms.ToTensor(), transforms.Normalize(mean_pre_trained,std_pre_trained)])
barilla_train_da = ScenesDataset('Dataset_data_augmentation','train_data_augmentation.txt',transform=transformss)
barilla_test_da = ScenesDataset('Dataset_data_augmentation','test_data_augmentation.txt',transform=transformss)
barilla_train_loader_da = torch.utils.data.DataLoader(barilla_train_da, batch_size=10, num_workers=0, shuffle=True)
barilla_test_loader_da = torch.utils.data.DataLoader(barilla_test_da, batch_size=10, num_workers=0)

# Utilizziamo AlexNet con i parametri pre-allenati e un numero di classi finali pari a 153

In [ ]:
net = models.alexnet(pretrained=True)
net.classifier[6] = nn.Linear(4096, num_classes) #Numero esatto di classi nel nostro dataset.
sum([p.numel() for p in net.parameters()])

# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_train_loader)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_test_loader)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

## Creiamo il dataframe e il knn

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)

if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()
net.eval()

barilla_train_loader_OB = torch.utils.data.DataLoader(barilla_train, batch_size=1, num_workers=0, shuffle=True)
barilla_test_loader_OB = torch.utils.data.DataLoader(barilla_test, batch_size=1, num_workers=0)


input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB, net)
df = pd.DataFrame(input_for_datafram_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)

In [ ]:
feature_test = extract_features(barilla_test_loader_OB, net)
print("Accuracy con rete preallenata e dataset base.")
print("1nn-->",accuracy(knn_1, feature_test))
print("3nn-->",accuracy(knn_3, feature_test))
print("5nn-->",accuracy(knn_5, feature_test))

# -----------------------------------------------------------------------------------------------

# Utilizziamo AlexNet con i parametri pre-allenati e un numero di classi finali pari a 1000 (valore di default)


In [ ]:
net = models.alexnet(pretrained=True)
sum([p.numel() for p in net.parameters()])

# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_train_loader)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_test_loader)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

# Creiamo il dataframe e il knn

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)

if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()
net.eval()

barilla_train_loader_OB = torch.utils.data.DataLoader(barilla_train, batch_size=1, num_workers=0, shuffle=True)
barilla_test_loader_OB = torch.utils.data.DataLoader(barilla_test, batch_size=1, num_workers=0)


input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB, net)
df = pd.DataFrame(input_for_datafram_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)

In [ ]:
feature_test = extract_features(barilla_test_loader_OB, net)
print("Accuracy con rete preallenata e dataset base.")
print("**************************1NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_1, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************3NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_3, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************5NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_5, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))


# -----------------------------------------------------------------------------------------------

# Utilizziamo AlexNet riallenando solamente l'ultimo layer con un numero di classi pari a 153 e 20 epoche di allenamento.


In [ ]:
net = models.alexnet(pretrained=True)
for param in net.parameters():
    param.requires_grad = False

net.classifier[6] = nn.Linear(4096, num_classes) #Numero esatto di classi nel nostro dataset.
sum([p.numel() for p in net.parameters()])
name_save = "last_layer_training_153classes_150epoche"

In [ ]:
path = "./" + name_save + ".pth"
my_file = Path(path)
training = False
if training == False and my_file.is_file():#Carico lo state altrimenti rialleno
    net.load_state_dict(torch.load(path))
    print("Caricato")
else:
    lenet_mnist, lenet_mnist_logs = train_classification(net, epochs=150, train_loader = barilla_train_loader,
                                                         test_loader = barilla_test_loader, exp_name = name_save)
    torch.save(net.state_dict(), path)

# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_train_loader)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_test_loader)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

# Creiamo il dataframe e il knn

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)

if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()
net.eval()

barilla_train_loader_OB = torch.utils.data.DataLoader(barilla_train, batch_size=1, num_workers=0, shuffle=True)
barilla_test_loader_OB = torch.utils.data.DataLoader(barilla_test, batch_size=1, num_workers=0)


input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB, net)
df = pd.DataFrame(input_for_datafram_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)

In [ ]:
feature_test = extract_features(barilla_test_loader_OB, net)
print("Accuracy con rete preallenata e dataset base.")
print("**************************1NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_1, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************3NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_3, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************5NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_5, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))


# -----------------------------------------------------------------------------------------------

# Utilizziamo AlexNet riallenando gli ultimi due layer con un numero di classi pari a 153 e 20 epoche di allenamento.


In [ ]:
net = models.alexnet(pretrained=True)
for param in net.parameters():
    param.requires_grad = False
    
net.classifier[4] = nn.Linear(4096, 4096) #Numero esatto di classi nel nostro dataset.
net.classifier[6] = nn.Linear(4096, 153) #Numero esatto di classi nel nostro dataset.
sum([p.numel() for p in net.parameters()])
name_save = "last_two_layers_training_153classes_150epoche"

In [ ]:
path = "./" + name_save + ".pth"
my_file = Path(path)

if training == False and my_file.is_file():#Carico lo state altrimenti rialleno
    net.load_state_dict(torch.load(path))
    print("Caricato")
else:
    lenet_mnist, lenet_mnist_logs = train_classification(net, epochs=150, train_loader = barilla_train_loader,
                                                         test_loader = barilla_test_loader, exp_name = name_save)
    torch.save(net.state_dict(), "./" + name_save + ".pth")

# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_train_loader)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_test_loader)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

# Creiamo il dataframe e il knn

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)

if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()
net.eval()

barilla_train_loader_OB = torch.utils.data.DataLoader(barilla_train, batch_size=1, num_workers=0, shuffle=True)
barilla_test_loader_OB = torch.utils.data.DataLoader(barilla_test, batch_size=1, num_workers=0)


input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB, net)
df = pd.DataFrame(input_for_datafram_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)

In [ ]:
feature_test = extract_features(barilla_test_loader_OB, net)
print("Accuracy con rete preallenata e dataset base.")
print("**************************1NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_1, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************3NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_3, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************5NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_5, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))


# -----------------------------------------------------------------------------------------------

# Rialleniamo alexnet con 153 classi in output. 150 epoche.


In [ ]:
net = models.alexnet()
net.classifier[6] = nn.Linear(4096, 153) #Numero esatto di classi nel nostro dataset.
sum([p.numel() for p in net.parameters()])
name_save = "retraining_all_layer_153classes_150epoche"

In [ ]:
path = "./" + name_save + ".pth"
my_file = Path(path)

if training == False and my_file.is_file():#Carico lo state altrimenti rialleno
    net.load_state_dict(torch.load(path))
    print("Caricato")
else:
    lenet_mnist, lenet_mnist_logs = train_classification(net, epochs=150, train_loader = barilla_train_loader,
                                                         test_loader = barilla_test_loader, exp_name = name_save)
    torch.save(net.state_dict(), "./" + name_save + ".pth")

# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_train_loader)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_test_loader)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

# Creiamo il dataframe e il knn

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)

if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()
net.eval()

barilla_train_loader_OB = torch.utils.data.DataLoader(barilla_train, batch_size=1, num_workers=0, shuffle=True)
barilla_test_loader_OB = torch.utils.data.DataLoader(barilla_test, batch_size=1, num_workers=0)


input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB, net)
df = pd.DataFrame(input_for_datafram_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)

In [ ]:
feature_test = extract_features(barilla_test_loader_OB, net)
print("Accuracy con rete preallenata e dataset base.")
print("**************************1NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_1, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************3NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_3, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************5NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_5, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))


# -----------------------------------------------------------------------------------------------

# <br><br><br> <br><br><br>

# Creiamo Oggetto Dataset e dataloader, sia base che data augmentation.

In [ ]:
transformss = transforms.Compose([transforms.ToTensor(), transforms.Normalize(mean_pre_trained,std_pre_trained)])
barilla_train_da = ScenesDataset('Dataset_data_augmentation','train_data_augmentation.txt',transform=transformss)
barilla_test_da = ScenesDataset('Dataset_data_augmentation','test_data_augmentation.txt',transform=transformss)
barilla_train_loader_da = torch.utils.data.DataLoader(barilla_train_da, batch_size=10, num_workers=0, shuffle=True)
barilla_test_loader_da = torch.utils.data.DataLoader(barilla_test_da, batch_size=10, num_workers=0)

# Utilizziamo AlexNet con i parametri pre-allenati e un numero di classi finali pari a 153

In [ ]:
net = models.alexnet(pretrained=True)
net.classifier[6] = nn.Linear(4096, 153) #Numero esatto di classi nel nostro dataset.
sum([p.numel() for p in net.parameters()])

# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_train_loader_da)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_test_loader_da)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

# Creiamo il dataframe e il knn

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)

if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()
#net.cpu()
net.eval()

barilla_train_loader_OB_da = torch.utils.data.DataLoader(barilla_train_da, batch_size=1, num_workers=0, shuffle=True)
barilla_test_loader_OB_da = torch.utils.data.DataLoader(barilla_test_da, batch_size=1, num_workers=0)


input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB_da, net)
df = pd.DataFrame(input_for_datafram_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)

In [ ]:
#feature_test = extract_features(barilla_test_loader_OB_da, net)
print("Accuracy con rete preallenata e dataset base.")
print("**************************1NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_1, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************3NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_3, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************5NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_5, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))


In [ ]:
feature_test_da = extract_features(barilla_test_loader_OB_da, net)
print("Accuracy con rete preallenata e dataset base.")
print("1nn-->",accuracy(knn_1, feature_test_da))
print("3nn-->",accuracy(knn_3, feature_test_da))
print("5nn-->",accuracy(knn_5, feature_test_da))
'''1nn--> 0.3511513157894737
3nn--> 0.37664473684210525
5nn--> 0.36101973684210525'''

# -----------------------------------------------------------------------------------------------

# Utilizziamo AlexNet con i parametri pre-allenati e un numero di classi finali pari a 1000 (valore di default)


In [ ]:
net = models.alexnet(pretrained=True)
sum([p.numel() for p in net.parameters()])

# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_train_loader_da)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_test_loader_da)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

# Creiamo il dataframe e il knn

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)

barilla_train_loader_OB_da = torch.utils.data.DataLoader(barilla_train_da, batch_size=1, num_workers=0, shuffle=True)
barilla_test_loader_OB_da = torch.utils.data.DataLoader(barilla_test_da, batch_size=1, num_workers=0)


if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()
#net.cpu()
net.eval()

input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB_da, net)
df = pd.DataFrame(input_for_datafram_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)

In [ ]:
feature_test = extract_features(barilla_test_loader_OB_da, net)
print("Accuracy con rete preallenata e dataset base.")
print("**************************1NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_1, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************3NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_3, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************5NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_5, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))


# -----------------------------------------------------------------------------------------------

# Utilizziamo AlexNet riallenando solamente l'ultimo layer con un numero di classi pari a 153 e 20 epoche di allenamento.


In [ ]:
net = models.alexnet(pretrained=True)
for param in net.parameters():
    param.requires_grad = False

net.classifier[6] = nn.Linear(4096, 153) #Numero esatto di classi nel nostro dataset.
sum([p.numel() for p in net.parameters()])
name_save = "last_layer_training_153classes_fulldataset_150epoche"

In [ ]:
path = "./" + name_save + ".pth"
my_file = Path(path)

if training == False and my_file.is_file():#Carico lo state altrimenti rialleno
    net.load_state_dict(torch.load(path))
    print("Caricato")
else:
    lenet_mnist, lenet_mnist_logs = train_classification(net, epochs=150, train_loader = barilla_train_loader_da,
                                                         test_loader = barilla_test_loader_da, exp_name = name_save)
    torch.save(net.state_dict(), "./" + name_save + ".pth")

# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_train_loader_da)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_test_loader_da)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

# Creiamo il dataframe e il knn

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)

if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()

net.eval()

input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB_da, net)
df = pd.DataFrame(input_for_datafram_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)
'''1nn--> 0.4440789473684211
3nn--> 0.4654605263157895
5nn--> 0.46875'''

In [ ]:
feature_test = extract_features(barilla_test_loader_OB_da, net)
print("Accuracy con rete preallenata e dataset base.")
print("**************************1NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_1, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************3NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_3, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************5NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_5, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))


# -----------------------------------------------------------------------------------------------

# Utilizziamo AlexNet riallenando gli ultimi due layer con un numero di classi pari a 153 e 20 epoche di allenamento.


In [ ]:
net = models.alexnet(pretrained=True)
for param in net.parameters():
    param.requires_grad = False
    
'''
net = models.resnet152(pretrained=True)
num_ftrs = net.fc.in_features
net.fc = nn.Linear(num_ftrs, n_classes)
'''
    
net.classifier[4] = nn.Linear(4096, 4096) #Numero esatto di classi nel nostro dataset.
net.classifier[6] = nn.Linear(4096, 153) #Numero esatto di classi nel nostro dataset.
sum([p.numel() for p in net.parameters()])
name_save = "last_two_layer_training_153classes_fulldataset150_epoche"

In [ ]:
path = "./" + name_save + ".pth"
my_file = Path(path)

if training == False and my_file.is_file():#Carico lo state altrimenti rialleno
    net.load_state_dict(torch.load(path))
    print("Caricato")
else:
    lenet_mnist, lenet_mnist_logs = train_classification(net, epochs=150, train_loader = barilla_train_loader_da,
                                                         test_loader = barilla_test_loader_da, exp_name = name_save)
    torch.save(net.state_dict(), "./" + name_save + ".pth")


# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_train_loader_da)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_test_loader_da)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

# Creiamo il dataframe e il knn

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)

if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()

net.eval()

input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB_da, net)
df = pd.DataFrame(input_for_datafram_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)

In [ ]:
feature_test = extract_features(barilla_test_loader_OB_da, net)
print("Accuracy con rete preallenata e dataset base.")
print("**************************1NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_1, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************3NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_3, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************5NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_5, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))


# -----------------------------------------------------------------------------------------------

# Rialleniamo alexnet con 153 classi in output. 20 epoche.


In [ ]:
net = models.alexnet()
net.classifier[6] = nn.Linear(4096, 153) #Numero esatto di classi nel nostro dataset.
sum([p.numel() for p in net.parameters()])
name_save = "retraining_alexnet_153classes_fulldataset_150epoche"

In [ ]:
path = "./" + name_save + ".pth"
my_file = Path(path)

if training == False and my_file.is_file():#Carico lo state altrimenti rialleno
    net.load_state_dict(torch.load(path))
    print("Caricato")
else:
    #net.load_state_dict(torch.load(path))
    lenet_mnist, lenet_mnist_logs = train_classification(net, epochs=150, train_loader = barilla_train_loader_da,
                                                         test_loader = barilla_test_loader_da, exp_name = name_save)
    torch.save(net.state_dict(), "./" + name_save + ".pth")

# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_train_loader_da)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_test_loader_da)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

# Creiamo il dataframe e il knn

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)


barilla_train_loader_OB_da = torch.utils.data.DataLoader(barilla_train_da, batch_size=1, num_workers=0, shuffle=True)
barilla_test_loader_OB_da = torch.utils.data.DataLoader(barilla_test_da, batch_size=1, num_workers=0)


if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()
net.eval()

input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB_da, net)
df = pd.DataFrame(input_for_datafram_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)

In [ ]:
feature_test = extract_features(barilla_test_loader_OB_da, net)
print("Accuracy con rete preallenata e dataset base.")
print("**************************1NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_1, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************3NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_3, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************5NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_5, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))


# -----------------------------------------------------------------------------------------------

In [ ]:
def extract_feature_single_image(path, net):
    #Apriamo l'immagine e la trasformiamo
    #carichiamo l'immagine utilizzando PIL e facciamo il resize a 3 canali.
    im = Image.open(path).convert("RGB")
    #Resize:
    im = im.resize((width,height))
    #se la trasfromazione è definita, applichiamola all'immagine
    transform = transforms.Compose([transforms.ToTensor(), transforms.Normalize(mean_pre_trained,std_pre_trained)])
    im = transform(im)       
     
    x=Variable(im, requires_grad=False)
    x = x.cpu()
    if torch.cuda.is_available():
        x = x.cuda()        
    output = net(x.unsqueeze(0))
    print(output)
    return output[0].detach()

In [ ]:
def get_predict_from_feature(feature, model):
    softmax = nn.Softmax(dim=1)
    model.eval()
    model.cpu()
    preds = []
    gts = []
    x=Variable(feature)
    x = x.cpu()
    #applichiamo la funzione softmax per avere delle probabilità
    if torch.cuda.is_available():
        x = x.cuda()
        model.cuda()
    pred = softmax(model(x)).data.cpu().numpy().copy()
    #return np.concatenate(preds),np.concatenate(gts)
    return pred

In [ ]:
def get_knn_predict_from_feature(feature, knn):
    pred_label = knn.predict(feature.cpu().numpy().reshape(1, -1))
    return pred_label

# Utilizziamo AlexNet riallenando solamente l'ultimo layer con un numero di classi pari a 1000 e 20 epoche di allenamento.


In [ ]:
net = models.alexnet(pretrained=True)
for param in net.parameters():
    param.requires_grad = False

net.classifier[6] = nn.Linear(4096, 1000) #Numero esatto di classi nel nostro dataset.
sum([p.numel() for p in net.parameters()])
#name_save = "last_layer_training_1000classes"

In [ ]:
path = "./" + name_save + ".pth"
my_file = Path(path)

if training == False and my_file.is_file():#Carico lo state altrimenti rialleno
    net.load_state_dict(torch.load(path))
    print("Caricato")
else:
    lenet_mnist, lenet_mnist_logs = train_classification(net, epochs=50, train_loader = barilla_train_loader,
                                                         test_loader = barilla_test_loader, exp_name = name_save)
    torch.save(net.state_dict(), path)

# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_train_loader)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification(net, barilla_test_loader)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

# Creiamo il dataframe e il knn

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)

if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()
net.eval()

barilla_train_loader_OB = torch.utils.data.DataLoader(barilla_train, batch_size=1, num_workers=0, shuffle=True)
barilla_test_loader_OB = torch.utils.data.DataLoader(barilla_test, batch_size=1, num_workers=0)


input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB, net)
df = pd.DataFrame(input_for_datafram_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)

In [ ]:
feature_test = extract_features(barilla_test_loader_OB, net)
print("Accuracy con rete preallenata e dataset base.")
print("1nn-->",accuracy(knn_1, feature_test))
print("3nn-->",accuracy(knn_3, feature_test))
print("5nn-->",accuracy(knn_5, feature_test))

# -----------------------------------------------------------------------------------------------

# RETE NOSTRA

In [20]:
class Multilayer_percetron(nn.Module):
    def __init__(self):
        super().__init__()
        self.features = nn.Sequential(
            nn.Linear(1000, 256, bias=True),
            nn.Linear(256, 184, bias=True),
            nn.ReLU(inplace = True),
            nn.Linear(184, 153, bias=True)
        )
        self.classifier =  nn.Sequential(
            nn.Softmax(dim=1)
        )
    def forward(self, xb, train = True):
        x = xb.view(-1,1000) 
        x = self.features(x)
        if train == False:
            x = self.classifier(x)
            pred = x.data.cpu().numpy().copy()
            print(pred)        
        return x

In [18]:
#Prendo le feature del train e del test con la network base senza allenare nessun layer.
net = models.alexnet(pretrained=True)
sum([p.numel() for p in net.parameters()])
net.cuda()

barilla_train_loader_OB_da = torch.utils.data.DataLoader(barilla_train, batch_size=1, num_workers=0, shuffle=True)
barilla_test_loader_OB_da = torch.utils.data.DataLoader(barilla_test, batch_size=1, num_workers=0)


feature_train = extract_features(barilla_train_loader_OB_da, net)
feature_test = extract_features(barilla_test_loader_OB_da, net)

Avviato extract_feature.
0 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234 235 236 237 238 239 240 241 242 243 244 245 246 247 248 249 250 251 252 253 254 255 256 257 258 259 260 261 262 263 264 265 266 267 268 269 270 2

In [21]:
#Creo la rete e la alleno.
our_net = Multilayer_percetron()
name_net = "our_net"
#our_net.load_state_dict(torch.load("./" + name_net + ".pth"))
train_classification_our_network(our_net, epochs = 150, train_loader = feature_train, test_loader = feature_test, lr = 0.001, exp_name = "our_net1")

Con cuda
[train] Epoch 1/150. Iteration 0/302. Loss: 4.75. Accuracy: 0.00					 4.7521653175354 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 1/302. Loss: 4.67. Accuracy: 0.00					 4.665386915206909 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 2/302. Loss: 4.74. Accuracy: 0.00					 4.744892120361328 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 3/302. Loss: 4.96. Accuracy: 0.00					 4.964881181716919 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 4/302. Loss: 4.87. Accuracy: 0.00					 4.8743672370910645 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 5/302. Loss: 4.97. Accuracy: 0.00					 4.9717780749003095 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 6/302. Loss: 5.13. Accuracy: 0.00					 5.129820755549839 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 7/302. Loss: 5.00. Accuracy: 0.00					 5.000990450382233 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 8/302. Loss: 5.02. Accuracy: 0.00					 5.0189098252190485 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 9/302

[train] Epoch 1/150. Iteration 76/302. Loss: 5.42. Accuracy: 0.00					 5.4166814692608725 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 77/302. Loss: 5.41. Accuracy: 0.00					 5.411010240897154 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 78/302. Loss: 5.40. Accuracy: 0.00					 5.404412607603435 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 79/302. Loss: 5.41. Accuracy: 0.00					 5.407397753000259 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 80/302. Loss: 5.39. Accuracy: 0.00					 5.393463588055269 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 81/302. Loss: 5.40. Accuracy: 0.00					 5.395343960785285 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 82/302. Loss: 5.40. Accuracy: 0.00					 5.40308946586517 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 83/302. Loss: 5.39. Accuracy: 0.00					 5.393216598601568 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 84/302. Loss: 5.39. Accuracy: 0.00					 5.385206054238712 0.0 None
Con cuda
[train] Epoch 1/150. Iteration 85/302

[train] Epoch 1/150. Iteration 144/302. Loss: 5.30. Accuracy: 0.01					 5.303402402483184 0.013793103448275862 None
Con cuda
[train] Epoch 1/150. Iteration 145/302. Loss: 5.30. Accuracy: 0.01					 5.304396059415112 0.0136986301369863 None
Con cuda
[train] Epoch 1/150. Iteration 146/302. Loss: 5.31. Accuracy: 0.01					 5.306659372485414 0.013605442176870748 None
Con cuda
[train] Epoch 1/150. Iteration 147/302. Loss: 5.30. Accuracy: 0.01					 5.303480530107343 0.013513513513513514 None
Con cuda
[train] Epoch 1/150. Iteration 148/302. Loss: 5.31. Accuracy: 0.01					 5.305883111569705 0.013422818791946308 None
Con cuda
[train] Epoch 1/150. Iteration 149/302. Loss: 5.30. Accuracy: 0.01					 5.303300601641337 0.013333333333333334 None
Con cuda
[train] Epoch 1/150. Iteration 150/302. Loss: 5.30. Accuracy: 0.01					 5.300374752638356 0.013245033112582781 None
Con cuda
[train] Epoch 1/150. Iteration 151/302. Loss: 5.30. Accuracy: 0.01					 5.297453166622865 0.013157894736842105 None
Con cuda
[t

Con cuda
[train] Epoch 1/150. Iteration 210/302. Loss: 5.23. Accuracy: 0.01					 5.232059073109197 0.009478672985781991 None
Con cuda
[train] Epoch 1/150. Iteration 211/302. Loss: 5.23. Accuracy: 0.01					 5.232484901851079 0.009433962264150943 None
Con cuda
[train] Epoch 1/150. Iteration 212/302. Loss: 5.23. Accuracy: 0.01					 5.229348432290163 0.009389671361502348 None
Con cuda
[train] Epoch 1/150. Iteration 213/302. Loss: 5.23. Accuracy: 0.01					 5.228483194502715 0.009345794392523364 None
Con cuda
[train] Epoch 1/150. Iteration 214/302. Loss: 5.23. Accuracy: 0.01					 5.229118481347728 0.009302325581395349 None
Con cuda
[train] Epoch 1/150. Iteration 215/302. Loss: 5.23. Accuracy: 0.01					 5.230221952553149 0.009259259259259259 None
Con cuda
[train] Epoch 1/150. Iteration 216/302. Loss: 5.23. Accuracy: 0.01					 5.23110344552774 0.009216589861751152 None
Con cuda
[train] Epoch 1/150. Iteration 217/302. Loss: 5.24. Accuracy: 0.01					 5.236333642530878 0.009174311926605505 None
C

[train] Epoch 1/150. Iteration 275/302. Loss: 5.21. Accuracy: 0.01					 5.207992884559908 0.010869565217391304 None
Con cuda
[train] Epoch 1/150. Iteration 276/302. Loss: 5.21. Accuracy: 0.01					 5.207929510502178 0.010830324909747292 None
Con cuda
[train] Epoch 1/150. Iteration 277/302. Loss: 5.21. Accuracy: 0.01					 5.206960032312132 0.01079136690647482 None
Con cuda
[train] Epoch 1/150. Iteration 278/302. Loss: 5.21. Accuracy: 0.01					 5.208640432699607 0.010752688172043012 None
Con cuda
[train] Epoch 1/150. Iteration 279/302. Loss: 5.21. Accuracy: 0.01					 5.207729476690292 0.010714285714285714 None
Con cuda
[train] Epoch 1/150. Iteration 280/302. Loss: 5.21. Accuracy: 0.01					 5.205665477230031 0.010676156583629894 None
Con cuda
[train] Epoch 1/150. Iteration 281/302. Loss: 5.20. Accuracy: 0.01					 5.204514950725204 0.010638297872340425 None
Con cuda
[train] Epoch 1/150. Iteration 282/302. Loss: 5.20. Accuracy: 0.01					 5.202766260915426 0.01060070671378092 None
Con cuda
[t

...

[train] Epoch 150/150. Iteration 243/302. Loss: 4.98. Accuracy: 0.01					 4.983759057326395 0.012295081967213115 None
Con cuda
[train] Epoch 150/150. Iteration 244/302. Loss: 4.98. Accuracy: 0.01					 4.983823986442721 0.012244897959183673 None
Con cuda
[train] Epoch 150/150. Iteration 245/302. Loss: 4.98. Accuracy: 0.01					 4.983696621607959 0.012195121951219513 None
Con cuda
[train] Epoch 150/150. Iteration 246/302. Loss: 4.98. Accuracy: 0.01					 4.983974796557716 0.012145748987854251 None
Con cuda
[train] Epoch 150/150. Iteration 247/302. Loss: 4.98. Accuracy: 0.01					 4.984064330977779 0.012096774193548387 None
Con cuda
[train] Epoch 150/150. Iteration 248/302. Loss: 4.98. Accuracy: 0.01					 4.984037667393205 0.012048192771084338 None
Con cuda
[train] Epoch 150/150. Iteration 249/302. Loss: 4.98. Accuracy: 0.01					 4.983969514846802 0.012 None
Con cuda
[train] Epoch 150/150. Iteration 250/302. Loss: 4.98. Accuracy: 0.01					 4.984081296806791 0.01195219123505976 None
Con cuda


Con cuda
[test] Epoch 150/150. Iteration 7/152. Loss: 5.13. Accuracy: 0.00					 5.126428306102753 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 8/152. Loss: 5.12. Accuracy: 0.00					 5.115164597829183 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 9/152. Loss: 5.11. Accuracy: 0.00					 5.108032464981079 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 10/152. Loss: 5.10. Accuracy: 0.00					 5.097823619842529 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 11/152. Loss: 5.09. Accuracy: 0.00					 5.091494083404541 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 12/152. Loss: 5.09. Accuracy: 0.00					 5.086281813108004 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 13/152. Loss: 5.11. Accuracy: 0.00					 5.114738464355469 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 14/152. Loss: 5.11. Accuracy: 0.00					 5.108997694651285 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 15/152. Loss: 5.10. Accuracy: 0.00					 5.104203164577484 0.0 None
Con cuda
[test] Epoch 150/150. 

[test] Epoch 150/150. Iteration 82/152. Loss: 5.03. Accuracy: 0.00					 5.03162950492767 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 83/152. Loss: 5.03. Accuracy: 0.00					 5.031476480620248 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 84/152. Loss: 5.03. Accuracy: 0.00					 5.031872126635383 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 85/152. Loss: 5.03. Accuracy: 0.00					 5.032642370046571 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 86/152. Loss: 5.03. Accuracy: 0.00					 5.032441939430675 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 87/152. Loss: 5.03. Accuracy: 0.00					 5.0322453325445 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 88/152. Loss: 5.03. Accuracy: 0.00					 5.032466304436158 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 89/152. Loss: 5.03. Accuracy: 0.00					 5.032142490810818 0.0 None
Con cuda
[test] Epoch 150/150. Iteration 90/152. Loss: 5.03. Accuracy: 0.00					 5.031543857448703 0.0 None
Con cuda
[test] Epoch 150/150. Iteration

[test] Epoch 150/150. Iteration 149/152. Loss: 5.03. Accuracy: 0.01					 5.030267779032389 0.006666666666666667 None
Con cuda
[test] Epoch 150/150. Iteration 150/152. Loss: 5.03. Accuracy: 0.01					 5.030032123161467 0.006622516556291391 None
Con cuda
[test] Epoch 150/150. Iteration 151/152. Loss: 5.03. Accuracy: 0.01					 5.030200390439284 0.006578947368421052 None
[test] Epoch 150/150. Iteration 151/152. Loss: 764590.46. Accuracy: 1000.00					
Pesi aggiornati.
Ho finito.


(Multilayer_percetron(
   (features): Sequential(
     (0): Linear(in_features=1000, out_features=256, bias=True)
     (1): Linear(in_features=256, out_features=184, bias=True)
     (2): ReLU(inplace)
     (3): Linear(in_features=184, out_features=153, bias=True)
   )
   (classifier): Sequential(
     (0): Softmax()
   )
 ),
 ({'train': [4752.1653175354,
    9330.773830413818,
    14234.676361083984,
    19859.524726867676,
    24371.836185455322,
    29830.668449401855,
    35908.74528884888,
    40007.92360305786,
    45170.188426971436,
    51151.88407897949,
    57469.669818878174,
    63382.513999938965,
    68368.95656585693,
    73416.81432723999,
    78510.02979278564,
    84892.73166656494,
    91720.02792358398,
    97377.50768661499,
    102909.3918800354,
    107532.93991088867,
    113535.46714782715,
    120064.67628479004,
    125013.88311386108,
    129279.24537658691,
    134450.4828453064,
    140861.16790771484,
    145780.30920028687,
    151327.00157165527,
    157

# Accuracy senza usare il knn

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification_our_network(net, our_net, barilla_train_loader_da)
print ("Accuracy aLexNet di train su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

In [ ]:
lenet_mnist_predictions, lenet_mnist_gt = test_model_classification_our_network(net, our_net, barilla_test_loader_da)
print ("Accuracy aLexNet di test su barillatestloader: %0.2f" % \
accuracy_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))
print("Precision_score-->")
print(precision_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Recall_score-->")
print(recall_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("F1_Score-->")
print(f1_score(lenet_mnist_gt,lenet_mnist_predictions.argmax(1), average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(lenet_mnist_gt,lenet_mnist_predictions.argmax(1)))

# Per knn su nostra rete.

In [ ]:
knn_1 = KNN(n_neighbors=1)
knn_3 = KNN(n_neighbors=3)
knn_5 = KNN(n_neighbors=5)

if torch.cuda.is_available():
    net = net.cuda()
    torch.cuda.empty_cache()
net.eval()

if torch.cuda.is_available():
    our_net = our_net.cuda()
    torch.cuda.empty_cache()
our_net.eval()

#barilla_train_loader_OB = torch.utils.data.DataLoader(barilla_train, batch_size=1, num_workers=0, shuffle=True)
#barilla_test_loader_OB = torch.utils.data.DataLoader(barilla_test, batch_size=1, num_workers=0)


#input_for_datafram_train, label_array_train = get_dataframe(barilla_train_loader_OB, our_net)
#Estraiamo le feature dalla rete e le passiamo al knn

feature_train = extract_features_our_network(extract_features(barilla_train_loader_OB, net), our_net)
feature_train, label_array_train = get_dataframe(barilla_train_loader_OB, our_net, feature_train)

df = pd.DataFrame(feature_train)
knn_1.fit(df, label_array_train)
knn_3.fit(df, label_array_train)
knn_5.fit(df, label_array_train)

In [ ]:
feature_test = extract_features_our_network(extract_features(barilla_test_loader_OB, net), our_net)
pred_label, target_label = get_pred_label_and_target_label(knn_1, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************3NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_3, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))

print("**************************5NN**************************")
pred_label, target_label = get_pred_label_and_target_label(knn_5, feature_test)
print("Accuracy-->", accuracy_score(target_label,pred_label))
print("Precision_score-->", precision_score(target_label,pred_label, average = 'macro'))
print("Recall_score-->", recall_score(target_label,pred_label, average = 'macro'))
print("F1_Score-->", f1_score(target_label,pred_label, average = 'macro'))
print("Matrice di confusione-->\n")
print(confusion_matrix(target_label,pred_label))



# -------------------------------------------------------------------------------------------------

# Allenamento dataset first level

In [ ]:
transformss = transforms.Compose([transforms.ToTensor(), transforms.Normalize(mean_pre_trained,std_pre_trained)])
barilla_train_fl = ScenesDataset('new_image_first_level','train_first_level.txt',transform=transformss)
barilla_test_fl = ScenesDataset('new_image_first_level','test_first_level.txt',transform=transformss)
barilla_train_loader_fl = torch.utils.data.DataLoader(barilla_train_fl, batch_size=10, num_workers=0, shuffle=True)
barilla_test_loader_fl = torch.utils.data.DataLoader(barilla_test_fl, batch_size=10, num_workers=0)